In [69]:
#import all necessary libraries and packages

import numpy as np 
import pandas as pd
from collections import defaultdict
import requests
import csv

from scipy.stats import norm

from bokeh.plotting import show, figure
from bokeh.models import ColumnDataSource, HoverTool
from bokeh.palettes import Viridis6


import math
import datetime

import matplotlib.pyplot as plt
import seaborn as sns
color = sns.color_palette()
%matplotlib inline

import plotly.offline as py
from plotly import tools
py.init_notebook_mode(connected=True)
import plotly.graph_objs as go
import plotly.express as px

pd.options.mode.chained_assignment = None
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 150)

In [2]:
#read data from the Covid Tracking project. More info can be found at www.covidtracking.com

#read state-by-state data that has information on positives, negatives, deaths, and daily increase values for each of these parameters
states_historical_df = pd.read_csv('https://covidtracking.com/api/v1/states/daily.csv')

#read state-by-state population data from the United States Census
states_pop = pd.read_csv('http://www2.census.gov/programs-surveys/popest/datasets/2010-2019/national/totals/nst-est2019-alldata.csv?#')
states_pop = states_pop[["NAME","POPESTIMATE2019"]][5:] #extract from states_pop just the state and corresponding population estimate for 2019.  


states_historical_df["date"] = pd.to_datetime(states_historical_df["date"], format="%Y%m%d").dt.date.astype(str)

#extract all unique date values in the date column
date_values = states_historical_df["date"].unique()

#This dictionary will be used for column remapping of state names later on as needed
state_map_dict = {'AL': 'Alabama',
 'AK': 'Alaska',
 'AS': 'American Samoa',
 'AZ': 'Arizona',
 'AR': 'Arkansas',
 'CA': 'California',
 'CO': 'Colorado',
 'CT': 'Connecticut',
 'DE': 'Delaware',
 'DC': 'District of Columbia',
 'FM': 'Federated States of Micronesia',
 'FL': 'Florida',
 'GA': 'Georgia',
 'GU': 'Guam',
 'HI': 'Hawaii',
 'ID': 'Idaho',
 'IL': 'Illinois',
 'IN': 'Indiana',
 'IA': 'Iowa',
 'KS': 'Kansas',
 'KY': 'Kentucky',
 'LA': 'Louisiana',
 'ME': 'Maine',
 'MH': 'Marshall Islands',
 'MD': 'Maryland',
 'MA': 'Massachusetts',
 'MI': 'Michigan',
 'MN': 'Minnesota',
 'MS': 'Mississippi',
 'MO': 'Missouri',
 'MT': 'Montana',
 'NE': 'Nebraska',
 'NV': 'Nevada',
 'NH': 'New Hampshire',
 'NJ': 'New Jersey',
 'NM': 'New Mexico',
 'NY': 'New York',
 'NC': 'North Carolina',
 'ND': 'North Dakota',
 'MP': 'Northern Mariana Islands',
 'OH': 'Ohio',
 'OK': 'Oklahoma',
 'OR': 'Oregon',
 'PW': 'Palau',
 'PA': 'Pennsylvania',
 'PR': 'Puerto Rico',
 'RI': 'Rhode Island',
 'SC': 'South Carolina',
 'SD': 'South Dakota',
 'TN': 'Tennessee',
 'TX': 'Texas',
 'UT': 'Utah',
 'VT': 'Vermont',
 'VI': 'Virgin Islands',
 'VA': 'Virginia',
 'WA': 'Washington',
 'WV': 'West Virginia',
 'WI': 'Wisconsin',
 'WY': 'Wyoming'}

#since some of our data uses full state names as opposed to the two letter denotion, we will also the invert state_map_dict dictionary
state_map_dict_inverted = {y:x for x,y in state_map_dict.items()}

state_list=list(state_map_dict.keys())

#use the state_map_dict_inverted dictionary to replace all state names with their 2 letter denotion
states_pop = states_pop.replace({"NAME": state_map_dict_inverted})

#merge the Covid Tracking project dataframe with the US Census Population dataframe
states_historical_df_pop = pd.merge(states_historical_df, states_pop, how='inner', left_on = 'state', right_on = 'NAME').drop(columns="NAME")

#Calculate Mortality Rate as the number of deaths normalized by population
states_historical_df_pop['Mortality Rate (%)']  = states_historical_df_pop["death"]*100/states_historical_df_pop["totalTestResults"]

states_historical_df_pop = states_historical_df_pop.round({'Mortality Rate (%)':2})

states_historical_df_pop


date state  positive  negative  pending  hospitalizedCurrently  \
0     2020-04-12    AK     272.0    7766.0      NaN                    NaN   
1     2020-04-11    AK     257.0    7475.0      NaN                    NaN   
2     2020-04-10    AK     246.0    7186.0      NaN                    NaN   
3     2020-04-09    AK     235.0    6988.0      NaN                    NaN   
4     2020-04-08    AK     226.0    6842.0      NaN                    NaN   
...          ...   ...       ...       ...      ...                    ...   
1995  2020-03-11    WY       0.0       NaN      NaN                    NaN   
1996  2020-03-10    WY       0.0       0.0      0.0                    NaN   
1997  2020-03-09    WY       0.0       NaN      NaN                    NaN   
1998  2020-03-08    WY       0.0       NaN      NaN                    NaN   
1999  2020-03-07    WY       0.0       NaN      NaN                    NaN   

      hospitalizedCumulative  inIcuCurrently  inIcuCumulative  \
0                       31.0             NaN              NaN   
1                       31.0             NaN              NaN   
2                       28.0             NaN              NaN   
3                       27.0             NaN              NaN   
4                       27.0             NaN              NaN   
...                      ...             ...              ...   
1995                     NaN             NaN              NaN   
1996                     NaN             NaN              NaN   
1997                     NaN             NaN              NaN   
1998                     NaN             NaN              NaN   
1999                     NaN             NaN              NaN   

      onVentilatorCurrently  ...  totalTestResults  posNeg fips deathIncrease  \
0                       NaN  ...            8038.0  8038.0    2           0.0   
1                       NaN  ...            7732.0  7732.0    2           1.0   
2                       NaN  ...            7432.0  7432.0    2           0.0   
3                       NaN  ...            7223.0  7223.0    2           0.0   
4                       NaN  ...            7068.0  7068.0    2           1.0   
...                     ...  ...               ...     ...  ...           ...   
1995                    NaN  ...               0.0     0.0   56           0.0   
1996                    NaN  ...               0.0     0.0   56           0.0   
1997                    NaN  ...               0.0     0.0   56           0.0   
1998                    NaN  ...               0.0     0.0   56           0.0   
1999                    NaN  ...               0.0     0.0   56           NaN   

      hospitalizedIncrease  negativeIncrease  positiveIncrease  \
0                      0.0             291.0              15.0   
1                      3.0             289.0              11.0   
2                      1.0             198.0              11.0   
3                      0.0             146.0               9.0   
4                      4.0             142.0              13.0   
...                    ...               ...               ...   
1995                   0.0               0.0               0.0   
1996                   0.0               0.0               0.0   
1997                   0.0               0.0               0.0   
1998                   0.0               0.0               0.0   
1999                   NaN               NaN               NaN   

      totalTestResultsIncrease  POPESTIMATE2019  Mortality Rate (%)  
0                        306.0           731545                0.10  
1                        300.0           731545                0.10  
2                        209.0           731545                0.09  
3                        155.0           731545                0.10  
4                        155.0           731545                0.10  
...                        ...              ...                 ...  
1995                       0.0        

In [3]:
#create list of plot dates from our earliest date to our latest date of the Covid Tracking project dataset 
plot_dates = pd.date_range(date_values.min(), date_values.max())

#this function allows us to filter the large multi-state Covid Tracking project dataset by a specific state
def statefilter(state_input):
    print(type(state_input))
    return states_historical_df_pop[states_historical_df_pop["state"]== state_input]


#create a dictionary of dataframes, df_by_state, that houses each state's covid and population data.  
#Then, to ensure that all states start data on the same date (some states started reporting later than others), 
#we expand each state's dataframe out to the earliest date in plot_dates and fill those un-entered dates with 0s

df_by_state = {}

for state in state_list:
    df_by_state[state] = statefilter(state)
    temp_state_df = df_by_state[state]
    datetime_index = pd.DatetimeIndex(temp_state_df['date'].values)
    temp_state_df.set_index(datetime_index, inplace=True)
    temp_state_df = temp_state_df.drop('date', 1)
    temp_state_df = temp_state_df.reindex(plot_dates, fill_value=None)
    temp_state_df["state"] = temp_state_df["state"].fillna(state)
    temp_state_df["positive"] = temp_state_df["positive"].fillna(0)
    temp_state_df["totalTestResults"] = temp_state_df["totalTestResults"].fillna(0)

    df_by_state[state] = temp_state_df

column_names = df_by_state["IL"].columns

df_by_state_cleaned = pd.DataFrame(columns = column_names)

#we reassign the cleaned state-by-state dataframes to 'df_by_state_cleaned' and reset the index column
for state in state_list:
    df_by_state_cleaned = df_by_state_cleaned.append(df_by_state[state])
    
df_by_state_cleaned = df_by_state_cleaned.rename_axis('date').reset_index()
df_by_state_cleaned

<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>
<class 'str'>


date state  positive  negative  pending  hospitalizedCurrently  \
0    2020-02-28    AL       0.0       NaN      NaN                    NaN   
1    2020-02-29    AL       0.0       NaN      NaN                    NaN   
2    2020-03-01    AL       0.0       NaN      NaN                    NaN   
3    2020-03-02    AL       0.0       NaN      NaN                    NaN   
4    2020-03-03    AL       0.0       NaN      NaN                    NaN   
...         ...   ...       ...       ...      ...                    ...   
2650 2020-04-08    WY     221.0    3843.0      NaN                    NaN   
2651 2020-04-09    WY     230.0    3920.0      NaN                    NaN   
2652 2020-04-10    WY     320.0    4736.0      NaN                    NaN   
2653 2020-04-11    WY     261.0    5198.0      NaN                    NaN   
2654 2020-04-12    WY     261.0    5198.0      NaN                    NaN   

      hospitalizedCumulative  inIcuCurrently  inIcuCumulative  \
0                        NaN             NaN              NaN   
1                        NaN             NaN              NaN   
2                        NaN             NaN              NaN   
3                        NaN             NaN              NaN   
4                        NaN             NaN              NaN   
...                      ...             ...              ...   
2650                    33.0             NaN              NaN   
2651                    34.0             NaN              NaN   
2652                    37.0             NaN              NaN   
2653                    37.0             NaN              NaN   
2654                    40.0             NaN              NaN   

      onVentilatorCurrently  ...  totalTestResults  posNeg  fips  \
0                       NaN  ...               0.0     NaN   NaN   
1                       NaN  ...               0.0     NaN   NaN   
2                       NaN  ...               0.0     NaN   NaN   
3                       NaN  ...               0.0     NaN   NaN   
4                       NaN  ...               0.0     NaN   NaN   
...                     ...  ...               ...     ...   ...   
2650                    NaN  ...            4064.0  4064.0  56.0   
2651                    NaN  ...            4150.0  4150.0  56.0   
2652                    NaN  ...            5056.0  5056.0  56.0   
2653                    NaN  ...            5459.0  5459.0  56.0   
2654                    NaN  ...            5459.0  5459.0  56.0   

     deathIncrease  hospitalizedIncrease  negativeIncrease  positiveIncrease  \
0              NaN                   NaN               NaN               NaN   
1              NaN                   NaN               NaN               NaN   
2              NaN                   NaN               NaN               NaN   
3              NaN                   NaN               NaN               NaN   
4              NaN                   NaN               NaN               NaN   
...            ...                   ...               ...               ...   
2650           0.0                   0.0              54.0               5.0   
2651           0.0                   1.0              77.0               9.0   
2652           0.0                   3.0             816.0              90.0   
2653           0.0                   0.0             462.0             -59.0   
2654           0.0                   3.0               0.0               0.0   

      totalTestResultsIncrease  POPESTIMATE2019  Mortality Rate (%)  
0                          NaN              NaN                 NaN  
1                          NaN              NaN                 NaN  
2                          NaN              NaN                 NaN  
3                          NaN              NaN                 NaN  
4                          NaN              NaN                 NaN  
...                        ...              ...                 ...  
2650                      59.0       

In [4]:
cumulative_df = states_historical_df_pop.groupby(["state","date"])["state","positive", "death", "negative", "total", "fips","POPESTIMATE2019"].sum().reset_index()

#cumulative_df["date"] = pd.to_datetime(cumulative_df["date"] , format="%Y-%m-%d").dt.date
#cumulative_df = cumulative_df.sort_values(by="date").reset_index(drop=True)
#start_date = datetime.date(2020, 3, 7)
#cumulative_df = cumulative_df[cumulative_df["date"]>=start_date]
#cumulative_df["date"] = cumulative_df["date"].astype(str)

#fig = px.choropleth(locations=cumulative_df["state"],
                    #color=cumulative_df["positive"]/cumulative_df["POPESTIMATE2019"]*100000, 
                    #locationmode="USA-states",
                    #scope="usa",
                    #animation_frame=cumulative_df["date"],
                    #color_continuous_scale='Reds',
                    #range_color=[0,100]
                    #autocolorscale=False,
                   #)


##layout = go.Layout(
#    title=go.layout.Title(
#        text="Cumulative count of positive COVID-19 cases in US states per 100,000 people",
#        x=0.5
#    ),
#    font=dict(size=14),
#)

#fig.update_layout(layout)
#fig.show()
cumulative_df[cumulative_df["state"]=="IL"]


/anaconda3/lib/python3.6/site-packages/ipykernel_launcher.py:1: FutureWarning:

Indexing with multiple keys (implicitly converted to a tuple of keys) will be deprecated, use a list instead.



state        date  positive  death  negative     total  fips  \
538    IL  2020-03-04       4.0    0.0     124.0     155.0    17   
539    IL  2020-03-05       5.0    0.0     165.0     197.0    17   
540    IL  2020-03-06       5.0    0.0     180.0     220.0    17   
541    IL  2020-03-07       6.0    0.0     191.0     241.0    17   
542    IL  2020-03-08       6.0    0.0     191.0     241.0    17   
543    IL  2020-03-09       7.0    0.0     191.0     242.0    17   
544    IL  2020-03-10      19.0    0.0     244.0     326.0    17   
545    IL  2020-03-11      19.0    0.0     244.0     326.0    17   
546    IL  2020-03-12      25.0    0.0     266.0     367.0    17   
547    IL  2020-03-13      32.0    0.0     294.0     418.0    17   
548    IL  2020-03-14      46.0    0.0     316.0     444.0    17   
549    IL  2020-03-15      64.0    0.0     449.0     708.0    17   
550    IL  2020-03-16      93.0    0.0     932.0    1025.0    17   
551    IL  2020-03-17     159.0    1.0    1340.0    1499.0    17   
552    IL  2020-03-18     288.0    1.0    1763.0    2051.0    17   
553    IL  2020-03-19     422.0    4.0    2725.0    3147.0    17   
554    IL  2020-03-20     585.0    5.0    3696.0    4281.0    17   
555    IL  2020-03-21     753.0    6.0    5488.0    6241.0    17   
556    IL  2020-03-22    1049.0    9.0    7271.0    8320.0    17   
557    IL  2020-03-23    1273.0   12.0    8583.0    9856.0    17   
558    IL  2020-03-24    1535.0   16.0    9934.0   11469.0    17   
559    IL  2020-03-25    1865.0   19.0   12344.0   14209.0    17   
560    IL  2020-03-26    2538.0   26.0   14093.0   16631.0    17   
561    IL  2020-03-27    3026.0   34.0   18516.0   21542.0    17   
562    IL  2020-03-28    3491.0   47.0   22000.0   25491.0    17   
563    IL  2020-03-29    4596.0   65.0   23166.0   27762.0    17   
564    IL  2020-03-30    5057.0   73.0   25389.0   30446.0    17   
565    IL  2020-03-31    5994.0   99.0   29231.0   35225.0    17   
566    IL  2020-04-01    6980.0  141.0   33404.0   40384.0    17   
567    IL  2020-04-02    7695.0  157.0   35961.0   43656.0    17   
568    IL  2020-04-03    8904.0  210.0   39144.0   48048.0    17   
569    IL  2020-04-04   10357.0  243.0   43224.0   53581.0    17   
570    IL  2020-04-05   11256.0  274.0   47727.0   58983.0    17   
571    IL  2020-04-06   12262.0  307.0   50680.0   62942.0    17   
572    IL  2020-04-07   13549.0  380.0   55183.0   68732.0    17   
573    IL  2020-04-08   15078.0  462.0   59988.0   75066.0    17   
574    IL  2020-04-09   16422.0  528.0   64435.0   80857.0    17   
575    IL  2020-04-10   17887.0  596.0   69640.0   87527.0    17   
576    IL  2020-04-11   19180.0  677.0   72969.0   92149.0    17   
577    IL  2020-04-12   20852.0  720.0   79883.0  100735.0    17   

     POPESTIMATE2019  
538         12671821  
539         12671821  
540         12671821  
541         12671821  
542         12671821  
543         12671821  
544         12671821  
545         12671821  
546         12671821  
547         12671821  
548         12671821  
549         12671821  
550         12671821  
551         12671821  
552         12671821  
553         12671821  
554         12671821  
555         12671821  
556         12671821  
557         12671821  
558         12671821  
559         12671821  
560         12671821  
561         12671821  
562         12671821  
563         12671821  
564         12671821  
565         12671821  
566         12671821  
567         12671821  
568         12671821  
569         12671821  
570         12671821  
571         12671821  
572         12671821  
573         12671821  
574         12671821  
575         12671821  
576         12671821  
577         12671821

In [5]:
fig = px.choropleth(locations=cumulative_df["state"],
                    color=cumulative_df["negative"], 
                    locationmode="USA-states",
                    scope="usa",
                    animation_frame=cumulative_df["date"],
                    color_continuous_scale='Greens',
                    range_color=[0,5000]
                    #autocolorscale=False,
                   )

layout = go.Layout(
    title=go.layout.Title(
        text="Cumulative count of COVID-19 cases in US states",
        x=0.5
    ),
    font=dict(size=14),
)

fig.update_layout(layout)
fig.show()

df_by_state["AL"]["positive"]

2020-02-28       0.0
2020-02-29       0.0
2020-03-01       0.0
2020-03-02       0.0
2020-03-03       0.0
2020-03-04       0.0
2020-03-05       0.0
2020-03-06       0.0
2020-03-07       0.0
2020-03-08       0.0
2020-03-09       0.0
2020-03-10       0.0
2020-03-11       0.0
2020-03-12       0.0
2020-03-13       1.0
2020-03-14       6.0
2020-03-15      12.0
2020-03-16      28.0
2020-03-17      36.0
2020-03-18      46.0
2020-03-19      68.0
2020-03-20      81.0
2020-03-21     124.0
2020-03-22     138.0
2020-03-23     167.0
2020-03-24     215.0
2020-03-25     283.0
2020-03-26     506.0
2020-03-27     587.0
2020-03-28     696.0
2020-03-29     806.0
2020-03-30     859.0
2020-03-31     981.0
2020-04-01    1077.0
2020-04-02    1233.0
2020-04-03    1432.0
2020-04-04    1580.0
2020-04-05    1796.0
2020-04-06    1968.0
2020-04-07    2119.0
2020-04-08    2369.0
2020-04-09    2769.0
2020-04-10    2968.0
2020-04-11    3191.0
2020-04-12    3525.0
Freq: D, Name: positive, dtype: float64

In [6]:
import plotly.express as px


fig = px.scatter(states_historical_df_pop, x="total", y="positive", animation_frame="date", animation_group="state",
           size="positive", color="state", hover_name="state",
           log_x=False, size_max=55, range_x=[0,250000], range_y=[0,100000])

layout = go.Layout(
    title=go.layout.Title(
        text="Total testing counts Vs Positive Counts over time",
        x=0.5
    ),
    font=dict(size=14),
#     width=800,
#     height=500,
    xaxis_title = "Total number of tests",
    yaxis_title = "Number of positive tests"
)

fig.update_layout(layout)
fig.show()
fig.write_html('positives_to_total_figure.html', auto_open=True)


In [7]:
df_by_state_cleaned["date"] = pd.to_datetime(df_by_state_cleaned["date"] , format="%m/%d/%Y").dt.date

df_by_state_cleaned = df_by_state_cleaned.sort_values(by="date").reset_index(drop = True)

df_by_state_cleaned["date"] = df_by_state_cleaned["date"].astype(str)

fig = px.scatter(df_by_state_cleaned, x="positive", y="death", animation_frame="date", animation_group="state",
           size="positive", color="state", hover_name="state",
           log_x=False, size_max=55, range_x=[0,120000], range_y=[0,3500])

layout = go.Layout(
    title=go.layout.Title(
        text="Positive test counts Vs deaths over time",
        x=0.5
    ),
    font=dict(size=14),
#     width=800,
#     height=500,
    xaxis_title = "Total number of positive tests",
    yaxis_title = "Number of deaths"
)

fig.update_layout(layout)
fig.update_layout(showlegend=False)

fig.show()
fig.write_html('deaths_to_positive_figure.html', auto_open=False)


In [34]:
states_historical_df_pop_NY = df_by_state_cleaned[df_by_state_cleaned["state"] == "IL"]

fig = px.line(states_historical_df_pop_NY, x="date", y="Mortality Rate (%)")

#fig.update_layout(yaxis_type="log")

layout = go.Layout(
    title=go.layout.Title(
        text="Illinois Positive Cases Over Time",
        x=0.5
    ),
    font=dict(size=14),
#     width=800,
#     height=500,
    xaxis_title = "Date",
    yaxis_title = "log(Positive Cases)"
)
fig.update_layout(layout)
fig.show()
#fig.write_html('positive_tests_over_time_figure.html', auto_open=False)
states_historical_df_pop_NY

date state  positive  negative  pending  hospitalizedCurrently  \
15    2020-02-28    IL       0.0       NaN      NaN                    NaN   
107   2020-02-29    IL       0.0       NaN      NaN                    NaN   
124   2020-03-01    IL       0.0       NaN      NaN                    NaN   
199   2020-03-02    IL       0.0       NaN      NaN                    NaN   
238   2020-03-03    IL       0.0       NaN      NaN                    NaN   
331   2020-03-04    IL       4.0     124.0     27.0                    NaN   
394   2020-03-05    IL       5.0     165.0     27.0                    NaN   
423   2020-03-06    IL       5.0     180.0     35.0                    NaN   
520   2020-03-07    IL       6.0     191.0     44.0                    NaN   
579   2020-03-08    IL       6.0     191.0     44.0                    NaN   
612   2020-03-09    IL       7.0     191.0     44.0                    NaN   
678   2020-03-10    IL      19.0     244.0     63.0                    NaN   
732   2020-03-11    IL      19.0     244.0     63.0                    NaN   
815   2020-03-12    IL      25.0     266.0     76.0                    NaN   
874   2020-03-13    IL      32.0     294.0     92.0                    NaN   
927   2020-03-14    IL      46.0     316.0     82.0                    NaN   
962   2020-03-15    IL      64.0     449.0    195.0                    NaN   
1003  2020-03-16    IL      93.0     932.0      NaN                    NaN   
1098  2020-03-17    IL     159.0    1340.0      NaN                    NaN   
1124  2020-03-18    IL     288.0    1763.0      NaN                    NaN   
1224  2020-03-19    IL     422.0    2725.0      NaN                    NaN   
1289  2020-03-20    IL     585.0    3696.0      NaN                    NaN   
1308  2020-03-21    IL     753.0    5488.0      NaN                    NaN   
1360  2020-03-22    IL    1049.0    7271.0      NaN                    NaN   
1456  2020-03-23    IL    1273.0    8583.0      NaN                    NaN   
1501  2020-03-24    IL    1535.0    9934.0      NaN                    NaN   
1566  2020-03-25    IL    1865.0   12344.0      NaN                    NaN   
1619  2020-03-26    IL    2538.0   14093.0      NaN                    NaN   
1706  2020-03-27    IL    3026.0   18516.0      NaN                    NaN   
1765  2020-03-28    IL    3491.0   22000.0      NaN                    NaN   
1782  2020-03-29    IL    4596.0   23166.0      NaN                    NaN   
1863  2020-03-30    IL    5057.0   25389.0      NaN                    NaN   
1907  2020-03-31    IL    5994.0   29231.0      NaN                    NaN   
1971  2020-04-01    IL    6980.0   33404.0      NaN                    NaN   
2046  2020-04-02    IL    7695.0   35961.0      NaN                    NaN   
2068  2020-04-03    IL    8904.0   39144.0      NaN                    NaN   
2135  2020-04-04    IL   10357.0   43224.0      NaN                    NaN   
2217  2020-04-05    IL   11256.0   47727.0      NaN                    NaN   
2250  2020-04-06    IL   12262.0   50680.0      NaN                    NaN   
2353  2020-04-07    IL   13549.0   55183.0      NaN                 3680.0   
2408  2020-04-08    IL   15078.0   59988.0      NaN                 3680.0   
2451  2020-04-09    IL   16422.0   64435.0      NaN                 3680.0   
2486  2020-04-10    IL   17887.0   69640.0      NaN                 3680.0   
2567  2020-04-11    IL   19180.0   72969.0      NaN                 3680.0   
2624  2020-04-12    IL   20852.0   79883.0      NaN                 3680.0   

      hospitalizedCumulative  inIcuCurrently  inIcuCumulative  \
15                       NaN             NaN              NaN   
107                      NaN             NaN              NaN   
124                      NaN             NaN              NaN   
199                      NaN             NaN              NaN   
238                      NaN             NaN              NaN   
331                      NaN     

In [16]:
county_historical_sum = pd.read_csv('https://github.com/nytimes/covid-19-data/raw/master/us-counties.csv')

#This needs to be grouped again !!!!!!!!
county_demographics_2019_df_sum = pd.read_csv('https://www2.census.gov/programs-surveys/popest/datasets/2010-2018/counties/asrh/cc-est2018-alldata.csv', encoding='ISO-8859-1')


county_demographics_2019_df_sum["HA_MALE"]=county_demographics_2019_df_sum["WA_MALE"]-county_demographics_2019_df_sum["NHWAC_MALE"]
county_demographics_2019_df_sum["HA_FEMALE"]=county_demographics_2019_df_sum["WA_FEMALE"]-county_demographics_2019_df_sum["NHWAC_FEMALE"]


#county_historical_sum['fips'] = county_historical_sum['fips'].astype(int)
county_demographics_2019_df_sum['COUNTY'] = county_demographics_2019_df_sum['COUNTY'].astype(int)

county_demographics_2019_df_sum['COUNTY'] = (county_demographics_2019_df_sum['STATE']*1000) + county_demographics_2019_df_sum['COUNTY']


#county_race_covid_2019_df = pd.merge(county_demographics_2019_df_sum, county_historical_sum, left_on = 'COUNTY', right_on = 'fips', how = "inner")


county_demographics_2019_df_sum

SUMLEV  STATE  COUNTY   STNAME         CTYNAME  YEAR  AGEGRP  TOT_POP  TOT_MALE  TOT_FEMALE  WA_MALE  WA_FEMALE  BA_MALE  BA_FEMALE  \
0           50      1    1001  Alabama  Autauga County     1       0    54571     26569       28002    21295      22002     4559       5130   
1           50      1    1001  Alabama  Autauga County     1       1     3579      1866        1713     1411       1316      362        317   
2           50      1    1001  Alabama  Autauga County     1       2     3991      2001        1990     1521       1526      399        374   
3           50      1    1001  Alabama  Autauga County     1       3     4290      2171        2119     1658       1620      431        406   
4           50      1    1001  Alabama  Autauga County     1       4     4290      2213        2077     1628       1585      502        424   
...        ...    ...     ...      ...             ...   ...     ...      ...       ...         ...      ...        ...      ...        ...   
656673      50     56   56045  Wyoming   Weston County    11      14      473       267         206      254        195        0          0   
656674      50     56   56045  Wyoming   Weston County    11      15      336       168         168      161        164        0          0   
656675      50     56   56045  Wyoming   Weston County    11      16      224       104         120      102        119        0          0   
656676      50     56   56045  Wyoming   Weston County    11      17      196        88         108       86        106        0          0   
656677      50     56   56045  Wyoming   Weston County    11      18      200        69         131       68        129        0          0   

        IA_MALE  IA_FEMALE  AA_MALE  AA_FEMALE  NA_MALE  NA_FEMALE  TOM_MALE  TOM_FEMALE  WAC_MALE  WAC_FEMALE  BAC_MALE  BAC_FEMALE  IAC_MALE  \
0           119        139      200        284       29         18       367         429     21633       22391      4704        5306       277   
1             5          3       13         15        1          0        74          62      1479        1368       405         362        23   
2            14          8       17         21        1          3        49          58      1570        1583       425         403        27   
3            15         12       23         18        4          1        40          62      1694        1681       453         436        29   
4            12          7       25         14        4          2        42          45      1664        1624       525         444        23   
...         ...        ...      ...        ...      ...        ...       ...         ...       ...         ...       ...         ...       ...   
656673        2          0        9          8        0          0         2           3       256         198         0           1         4   
656674        1          2        2          1        0          0         4           1       165         165         1           0         4   
656675        0          1        0          0        0          0         2           0       104         119         0           0         2   
656676        1          2        0          0        0          0         1           0        87         106         0           0         2   
656677        1          0        0          1        0          0         0           1        68         130         0           1         1   

        IAC_FEMALE  AAC_MALE  AAC_FEMALE  NAC_MALE  NAC_FEMALE  NH_MALE  NH_FEMALE  NHWA_MALE  NHWA_FEMALE  NHBA_MALE  NHBA_FEMALE  NHIA_MALE  \
0              314       300         409        42          37    25875      27386      20709        21485       4512         5091        103   
1               18        34          28         3           1     1778       1651       1337         1260        356          313          2   
2               19        32          42         3           4     1933       1916       1460         1

In [13]:
county_race_covid_2019_df
#Rename COUNTY to COUNTY FIPS and STATE to STATE FIPS, then move state and county to the front.  thanks bro
#county_race_covid_2019_df['STATE'] = county_race_covid_2019_df['STATE'].astype(str)

#county_race_covid_2019_df = county_race_covid_2019_df.replace({"STATE": state_codes_swap})

county_race_covid_2019_df = county_race_covid_2019_df.rename(columns={'COUNTY': 'COUNTY_FIPS', 'STATE': 'STATE_FIPS'})
temp = county_race_covid_2019_df['state']
county_race_covid_2019_df.drop(labels=['state'], axis=1, inplace = True)
county_race_covid_2019_df.insert(0, 'state', temp)
temp2 = county_race_covid_2019_df['county']
county_race_covid_2019_df.drop(labels=['county'], axis=1, inplace = True)
county_race_covid_2019_df.insert(1, 'county', temp2)





In [14]:

county_race_covid_2019_df["Total"] = county_race_covid_2019_df["TOT_MALE"]+county_race_covid_2019_df["TOT_FEMALE"]
county_race_covid_2019_df["Cases per 1000"] = county_race_covid_2019_df["cases"]/county_race_covid_2019_df["Total"]*1000
county_race_covid_2019_df["Cases per 100"] = county_race_covid_2019_df["cases"]/county_race_covid_2019_df["Total"]*100



county_race_covid_2019_df["White"] = county_race_covid_2019_df["WA_MALE"]+county_race_covid_2019_df["WA_FEMALE"]
county_race_covid_2019_df["%White"] = county_race_covid_2019_df["White"]/county_race_covid_2019_df["Total"]*100

county_race_covid_2019_df["Black"] = county_race_covid_2019_df["BA_MALE"]+county_race_covid_2019_df["BA_FEMALE"]
county_race_covid_2019_df["%Black"] = county_race_covid_2019_df["Black"]/county_race_covid_2019_df["Total"]*100

county_race_covid_2019_df["Asian"] = county_race_covid_2019_df["AA_MALE"]+county_race_covid_2019_df["AA_FEMALE"]
county_race_covid_2019_df["%Asian"] = county_race_covid_2019_df["Asian"]/county_race_covid_2019_df["Total"]*100

county_race_covid_2019_df["American Indian"] = county_race_covid_2019_df["IA_MALE"]+county_race_covid_2019_df["IA_FEMALE"]
county_race_covid_2019_df["%American Indian"] = county_race_covid_2019_df["American Indian"]/county_race_covid_2019_df["Total"]*100

county_race_covid_2019_df["Hispanic"] = county_race_covid_2019_df["HA_MALE"]+county_race_covid_2019_df["HA_FEMALE"]
county_race_covid_2019_df["%Hispanic"] = county_race_covid_2019_df["Hispanic"]/county_race_covid_2019_df["Total"]*100

county_race_covid_2019_df["Pacific Islander"] = county_race_covid_2019_df["NA_MALE"]+county_race_covid_2019_df["NA_FEMALE"]
county_race_covid_2019_df["%Pacific Islander"] = county_race_covid_2019_df["Pacific Islander"]/county_race_covid_2019_df["Total"]*100


county_race_covid_2019_df_plot = county_race_covid_2019_df[county_race_covid_2019_df["state"]=="Illinois"]

county_race_covid_2019_df_plot
county_race_covid_2019_df

state      county  STATE_FIPS  COUNTY_FIPS  TOT_POP  TOT_MALE  \
0     Alabama     Autauga           1         1001   111202     53990   
1     Alabama     Baldwin           1         1003   436044    211314   
2     Alabama     Barbour           1         1005    49762     26266   
3     Alabama        Bibb           1         1007    44800     23842   
4     Alabama      Blount           1         1009   115680     57000   
...       ...         ...         ...          ...      ...       ...   
2644  Wyoming    Sublette          56        56035    19626     10590   
2645  Wyoming  Sweetwater          56        56037    86102     44304   
2646  Wyoming       Teton          56        56039    46162     23818   
2647  Wyoming       Uinta          56        56041    40598     20570   
2648  Wyoming    Washakie          56        56043    15770      7976   

      TOT_FEMALE  WA_MALE  WA_FEMALE  BA_MALE  ...  Black     %Black  Asian  \
0          57212    41718      43602    10306  ...  21830  19.630942   1362   
1         224730   184942     195660    18800  ...  38984   8.940382   5016   
2          23496    12820      11598    12740  ...  24084  48.398376    226   
3          20958    17524      16898     5908  ...   9540  21.294643    106   
4          58680    54614      56298     1014  ...   1900   1.642462    370   
...          ...      ...        ...      ...  ...    ...        ...    ...   
2644        9036    10116       8664      116  ...    176   0.896770    144   
2645       41798    41668      39126      656  ...   1184   1.375113    870   
2646       22344    22714      21228      200  ...    350   0.758199    652   
2647       20028    19636      19076      156  ...    336   0.827627    192   
2648        7794     7556       7344       50  ...     80   0.507292    130   

        %Asian  American Indian  %American Indian  Hispanic  %Hispanic  \
0     1.224798              534          0.480207       996   0.895667   
1     1.150343             3368          0.772399     11578   2.655237   
2     0.454162              328          0.659137      1256   2.524014   
3     0.236607              196          0.437500       590   1.316964   
4     0.319848              756          0.653527      9030   7.806017   
...        ...              ...               ...       ...        ...   
2644  0.733721              234          1.192296      1066   5.431570   
2645  1.010429             1330          1.544680     11172  12.975308   
2646  1.412417              422          0.914172      5788  12.538452   
2647  0.472930              576          1.418789      2660   6.552047   
2648  0.824350              286          1.813570      1656  10.500951   

      Pacific Islander  %Pacific Islander  
0                  124           0.111509  
1                  292           0.066966  
2                   92           0.184880  
3                   52           0.116071  
4                  140           0.121024  
...                ...                ...  
2644                 8           0.040762  
2645               136           0.157952  
2646                70           0.151640  
2647                60           0.147791  
2648                16           0.101458  

[2649 rows x 39 columns]

In [15]:
fig = px.scatter(county_race_covid_2019_df_plot, x="%Black", y="Cases per 100", hover_name= "COUNTY_FIPS",
           log_y=False, size_max=55, range_x=[0,250000], range_y=[1,100000])


#fig.add_scatter(x=county_race_covid_2019_df_plot["%White"], y=county_race_covid_2019_df_plot["cases"], mode = "markers") # Not what is desired - need a line 

fig.show()

In [16]:
cook_county_deaths = pd.read_csv("https://datacatalog.cookcountyil.gov/api/views/cjeq-bs86/rows.csv?accessType=DOWNLOAD",dtype = {"Incident Zip Code" : "str","Residence_Zip" : "str"})

cook_county_deaths = cook_county_deaths[["Case Number","Date of Death", "Age", "Gender", "Race", "Latino", "Manner of Death", "Primary Cause", "Primary Cause Line A", "Primary Cause Line B", "Primary Cause Line C", "Secondary Cause", "Incident City", "Incident Zip Code", "longitude", "latitude", "location", "Residence City", "Residence_Zip", "OBJECTID"]]

filter_statement = (cook_county_deaths["Primary Cause"].str.contains('NOVEL',na=False)) | (cook_county_deaths["Primary Cause Line A"].str.contains('NOVEL',na=False)) | (cook_county_deaths["Primary Cause Line B"].str.contains('NOVEL',na=False)) | (cook_county_deaths["Primary Cause Line C"].str.contains('NOVEL',na=False)) | (cook_county_deaths['Secondary Cause'].str.contains('NOVEL',na=False))

cook_county_deaths_cleaned = cook_county_deaths[filter_statement]


cook_county_deaths_cleaned_race = cook_county_deaths_cleaned.groupby(["Race"])["Case Number"].count().reset_index()
cook_county_deaths_cleaned_age = cook_county_deaths_cleaned.groupby(["Age"])["Case Number"].count().reset_index()

cook_county_deaths_cleaned_race["Racial Percentage"] = cook_county_deaths_cleaned_race["Case Number"]/cook_county_deaths_cleaned_race["Case Number"].sum()*100
cook_county_deaths_cleaned_age["Age Percentage"] = cook_county_deaths_cleaned_age["Case Number"]/cook_county_deaths_cleaned_race["Case Number"].sum()*100

cook_county_deaths_cleaned_age

bins= [0,5,15,20,30,40,50,60,70,105]
labels = ['0-5 yrs','5-15 yrs','15-20 yrs','20-30 yrs','30-40 yrs', "40-50 yrs", "50-60 yrs", "60-70 yrs", "70-105 yrs"]
cook_county_deaths_cleaned_age['AgeGroup'] = pd.cut(cook_county_deaths_cleaned_age['Age'], bins=bins, labels=labels, right=False)

cook_county_deaths_cleaned_age = cook_county_deaths_cleaned_age.groupby(["AgeGroup"])["Age Percentage"].sum().reset_index()
cook_county_deaths_cleaned_age

cook_county_deaths_cleaned_race


Race  Case Number  Racial Percentage
0    Asian            9           1.882845
1    Black          247          51.673640
2    Other           12           2.510460
3  Unknown            6           1.255230
4    White          204          42.677824

In [17]:
fig = px.pie(cook_county_deaths_cleaned_race, values='Racial Percentage', names='Race', color_discrete_sequence=px.colors.sequential.RdBu, title = "Cook County COVID19 Deaths by Race")


fig.update_traces(hoverinfo='label+percent', textinfo='percent+label', textfont_size=20,
                  marker=dict(line=dict(color='#000000', width=2)))
layout2 = go.Layout(
                    annotations = [dict(xref='paper',
                                        yref='paper',
                                        x=1.2, y=-0.25,
                                        showarrow=False,
                                        text ='El Khatib, data courtesy of Cook County Medical Examiner Case Archive')])

fig.update_layout(layout2)

fig.show()

In [18]:


fig = px.bar(cook_county_deaths_cleaned_age, title = "Cook County COVID19 Deaths by Age", x='AgeGroup', y='Age Percentage',
             hover_data=['Age Percentage'], color='AgeGroup', height=400, text = "Age Percentage", color_discrete_sequence=px.colors.sequential.RdBu)

fig.update_traces(texttemplate='%{text:.2s}%', textposition='outside')
fig.update_layout(uniformtext_minsize=8, uniformtext_mode='hide')
layout = go.Layout(
    font=dict(size=14),
    width=1050,
     height=550,
    xaxis_title = "Age Bracket",
    yaxis_title = "Percentage of COVID19 Deaths")
fig.update_layout(layout)
fig.update_layout(showlegend=False)

fig.show()

In [11]:
import geopandas as gpd
data = gpd.read_file('usa-hospital-beds_dataset.geojson')
bed_data = pd.DataFrame(data)
bed_data


OBJECTID                                      HOSPITAL_NAME                   HOSPITAL_TYPE              HQ_ADDRESS HQ_ADDRESS1  \
0         5001                             The Willough at Naples            Psychiatric Hospital      9001 Tamiami Trl E        None   
1         5002                             Spring Mountain Sahara            Psychiatric Hospital       5460 W Sahara Ave        None   
2         5003                             Moab Regional Hospital        Critical Access Hospital        450 Williams Way        None   
3         5004  AdventHealth Durand (FKA Chippewa Valley Hospi...        Critical Access Hospital          1220 3rd Ave W        None   
4         5005                         St Michaels Hospital Avera        Critical Access Hospital          410 W 16th Ave        None   
...        ...                                                ...                             ...                     ...         ...   
6610      3996                             Sentara Obici Hospital  Short Term Acute Care Hospital        2800 Godwin Blvd        None   
6611      3997            Sentara Virginia Beach General Hospital  Short Term Acute Care Hospital  1060 First Colonial Rd        None   
6612      3998                          Winchester Medical Center  Short Term Acute Care Hospital         1840 Amherst St        None   
6613      3999                         Othello Community Hospital        Critical Access Hospital          315 N 14th Ave        None   
6614      4000                        Tri-State Memorial Hospital        Critical Access Hospital       1221 Highland Ave        None   

             HQ_CITY HQ_STATE HQ_ZIP_CODE     COUNTY_NAME    STATE_NAME STATE_FIPS CNTY_FIPS   FIPS  NUM_LICENSED_BEDS  NUM_STAFFED_BEDS  \
0             Naples       FL       34113         Collier       Florida         12       021  12021               87.0              87.0   
1          Las Vegas       NV       89146           Clark        Nevada         32       003  32003               30.0              30.0   
2               Moab       UT       84532           Grand          Utah         49       019  49019               17.0              17.0   
3             Durand       WI       54736           Pepin     Wisconsin         55       091  55091               25.0              25.0   
4            Tyndall       SD       57066       Bon Homme  South Dakota         46       009  46009               25.0              25.0   
...              ...      ...         ...             ...           ...        ...       ...    ...                ...               ...   
6610         Suffolk       VA       23434         Suffolk      Virginia         51       800  51800              178.0             155.0   
6611  Virginia Beach       VA       23454  Virginia Beach      Virginia         51       810  51810              273.0             227.0   
6612      Winchester       VA       22601      Winchester      Virginia         51       840  51840              455.0             389.0   
6613         Othello       WA       99344           Adams    Washington         53       001  53001               49.0              16.0   
6614       Clarkston       WA       99403          Asotin    Washington         53       003  53003               62.0              25.0   

      NUM_ICU_BEDS  ADULT_ICU_BEDS  PEDI_ICU_BEDS  BED_UTILIZATION  Potential_Increase_In_Bed_Capac  AVG_VENTILATOR_USAGE  \
0                0               0            0.0         0.943600                                0                   0.0   
1                1               1            0.0         0.786119                                0                   2.0   
2                3               3            0.0         0.351974                                0                   2.0   
3                4               4            0.0         0.142904                                0                   0.0   
4                4               4            0.0      

In [12]:
bed_data_drop_rows = bed_data[bed_data['FIPS'].isnull()].index
bed_data.drop(bed_data_drop_rows , inplace=True)

bed_data['FIPS'] = bed_data['FIPS'].astype(int)
county_race_covid_2019_df['COUNTY_FIPS'] = county_race_covid_2019_df['COUNTY_FIPS'].astype(int)


bed_data_demographic = pd.merge(bed_data, county_race_covid_2019_df, left_on = 'FIPS', right_on = 'COUNTY_FIPS', how = "inner")


NameError: name 'county_race_covid_2019_df' is not defined

In [10]:
bed_data_demographic.head(500)

NameError: name 'bed_data_demographic' is not defined

In [133]:
import plotly.figure_factory as ff

colorscale = ["#f7fbff", "#ebf3fb", "#deebf7", "#d2e3f3", "#c6dbef", "#b3d2e9", "#9ecae1",
    "#85bcdb", "#6baed6", "#57a0ce", "#4292c6", "#3082be", "#2171b5", "#1361a9",
    "#08519c", "#0b4083", "#08306b"
]
endpts = list(np.linspace(1, 12, len(colorscale) - 1))
#fips = bed_data_demographic['FIPS'].tolist()
#values = bed_data_demographic['Unemployment Rate (%)'].tolist()


fig = ff.create_choropleth(
    fips=bed_data_demographic["FIPS"], values = bed_data_demographic["NUM_LICENSED_BEDS"], scope=['usa'],
    binning_endpoints=endpts, colorscale=colorscale,
    show_state_data=False,
    show_hover=True,
    asp = 2.9,
    title_text = 'USA',
    legend_title = 'NUM OF LICENSED BEDS'
)
fig.layout.template = None
fig.show()

ERROR:root:An unexpected error occurred while tokenizing input
The following traceback may be corrupted or invalid
The error message is: ('EOF in multi-line string', (1, 0))



ValueError: 
The create_choropleth figure factory requires the plotly-geo package.
Install using pip with:

$ pip install plotly-geo

Or, install using conda with

$ conda install -c plotly plotly-geo
